# Exercise 5: Graph Algorithms

In [43]:
# Install packages incase you cannot import
import unittest
import sys
import heapq

## Implement recursive depth-first search

In [44]:
class Graph:
    def __init__(self, vertices):
        self.V = vertices
        self.adj = {} # Stores the adjacency lists in form {<from_vertex>: [<to_vertex>,<to_vertex>]} (e.g., {A: [B,C]})
        self.vt = {} # Stores the starting times in form {<vertex>: <starting_time>} (e.g., {A: 1})
        self.ft = {} # Stores the finish times in same form as starting times
        self.state = {} # Stores the state which is either visited or unvisited (we omit the finished state) same form as starting times
        self.time = 0
        for v in self.V:
            self.adj[v] = [] 
            self.vt[v] = 0 
            self.ft[v] = 0 
            self.state[v] = 0 

    def add_edge(self, from_vertex, to_vertex) -> None:
        self.adj[from_vertex].append(to_vertex)

    def initialize(self):
        # Helpfer function to reset ft, vt, and state for the graph
        self.vt = {k: 0 for k in self.vt.keys()}
        self.ft = {k: 0 for k in self.ft.keys()}
        self.state = {k: 0 for k in self.state.keys()}
        self.time = 0

def dfs(G):
    G.initialize()
    for v in G.V:
        if G.state[v] == 0:
            dfs_visit(G, v)
        
def dfs_visit(G, u):
    G.time += 1
    G.state[u] = 1
    G.vt[u] = G.time
    for w in G.adj[u]:
        if G.state[w] == 0:
            dfs_visit(G, w)
    G.time = G.time + 1
    G.ft[u] = G.time



Test DFS by running the following cell

In [45]:
# Test cases (test only proper execution of the method. Does not test for complexity).
class TestDfs(unittest.TestCase):
    
    def testDFS1(self):
        G=Graph(["m","n","o","p","q","r","s","t","u","v","w","x","y","z"])   
        G.add_edge("m","q")
        G.add_edge("m","r")
        G.add_edge("m","x")
        G.add_edge("n","q")
        G.add_edge("n","o")
        G.add_edge("n","u")
        G.add_edge("o","r")
        G.add_edge("o","s")
        G.add_edge("p","o")
        G.add_edge("p","s")
        G.add_edge("q","t")
        G.add_edge("r","u")
        G.add_edge("r","y")
        G.add_edge("s","r")
        G.add_edge("u","t")
        G.add_edge("v","w")
        G.add_edge("w","z")
        G.add_edge("y","v")
        G.add_edge("y","x")
        dfs(G)
        gold_vt = {'m': 1, 'n': 21, 'o': 22, 'p': 27, 'q': 2, 'r': 6, 's': 23, 't': 3, 'u': 7, 'v': 10, 'w': 11, 'x': 16, 'y': 9, 'z': 12}
        gold_ft = {'m': 20, 'n': 26, 'o': 25, 'p': 28, 'q': 5, 'r': 19, 's': 24, 't': 4, 'u': 8, 'v': 15, 'w': 14, 'x': 17, 'y': 18, 'z': 13}
        for k in G.V:
            self.assertEqual(G.vt[k], gold_vt[k])
            self.assertEqual(G.ft[k], gold_ft[k])

    def testDFS2(self):
        G=Graph([])
        dfs(G)

    def testDFS3(self):   
        G=Graph(["a","b","c"])
        G.add_edge("a","b")
        G.add_edge("b","c")
        G.add_edge("c","a")
        dfs(G)
        gold_vt = {"a": 1, "b": 2, "c": 3}
        gold_ft = {"a": 6, "b": 5, "c": 4}
        for k in G.V:
            self.assertEqual(G.vt[k], gold_vt[k])
            self.assertEqual(G.ft[k], gold_ft[k])

# Run the test cases
unittest.main(argv=[''], verbosity=2, exit=False)
# Clean up
del TestDfs

testDFS1 (__main__.TestDfs) ... ok
testDFS2 (__main__.TestDfs) ... ok
testDFS3 (__main__.TestDfs) ... ok



----------------------------------------------------------------------
Ran 3 tests in 0.006s

OK


## Implement Dijkstra´s algorithm

In [46]:
# Implementation of priority queue
class PriorityQueue:
    def __init__(self):
        self._heap = []

    def push(self, item, priority):
         # Adds an element to the PriorityQueue and maintains the heap property
        heapq.heappush(self._heap, (priority, item))

    def pop(self):
        # Extracts the minimum element from the PriorityQueue and maintains the heap property
        if not self.is_empty():
            return heapq.heappop(self._heap)[1]
        else:
            raise IndexError("pop from an empty priority queue")

    def decrease_key(self, item, new_priority):
        # Find the index of the item in the heap
        for i, (priority, current_item) in enumerate(self._heap):
            if current_item == item:
                # Update the priority
                self._heap[i] = (new_priority, current_item)
                # Restore the heap property
                heapq.heapify(self._heap)
                return

    def is_empty(self):
        return len(self._heap) == 0

class Graph:
    def __init__(self, vertices):
        self.V = vertices
        self.adj = {} # Stores the adjacency lists in form {<from_vertex>: [(<to_vertex>, weight),(<to_vertex>, weight)]} (e.g., {A: [(B, 1),(C, 3)]})
        self.dist = {} # Stores the distances in form {<vertex>: <distance>} (e.g., {A: 1})
        self.prev = {} # Stores the previous node in form {<vertex>: <vertex>} (e.g., {A: B})
        for v in self.V:
            self.adj[v] = []
            self.dist[v] = sys.maxsize
            self.prev[v] = None

    def add_edge(self, from_vertex, to_vertex, weight) -> None:
        self.adj[from_vertex].append((to_vertex, weight))

    def initialize(self):
        for v in self.V:
            self.dist[v] = sys.maxsize
            self.prev[v] = None

def dijkstra(G, s):
    G.initialize()
    G.dist[s] = 0
    Q = PriorityQueue()
    for v, w in G.dist.items():
        Q.push(v, w)
    while not Q.is_empty():
        u = Q.pop()
        for v, w in G.adj[u]:
            # Relax
            new_dist = G.dist[u] + w
            if G.dist[v] > new_dist:
                Q.decrease_key(v, new_dist)
                G.dist[v] = new_dist
                G.prev[v] = u

Test Dijkstra by running the following cell

In [47]:
# Test cases
class TestDijkstra(unittest.TestCase):
    def testDijkstra1(self):
        g = Graph([0,1,2,3,4])
        g.add_edge(0, 1, 10)
        g.add_edge(0, 3, 5)
        g.add_edge(1, 2, 1)
        g.add_edge(1, 3, 5)
        g.add_edge(2, 4, 4)
        g.add_edge(3, 1, 3)
        g.add_edge(3, 2, 9)
        g.add_edge(3, 4, 2)
        g.add_edge(4, 0, 7)
        g.add_edge(3, 2, 6)
        dijkstra(g, 0)
        gold_dist = {0: 0, 1: 8, 2: 9, 3: 5, 4: 7}
        gold_prev = {0: None, 1: 3, 2: 1, 3: 0, 4: 3}
        for v in g.V:
            self.assertEqual(g.dist[v], gold_dist[v])
            self.assertEqual(g.prev[v], gold_prev[v])
    
    def testDijkstra2(self):
        g = Graph([0, 1])
        dijkstra(g, 0)
        gold_dist = {0: 0, 1: sys.maxsize}
        gold_prev = {0: None, 1: None}
        for v in g.V:
            self.assertEqual(g.dist[v], gold_dist[v])
            self.assertEqual(g.prev[v], gold_prev[v])

# Run the test cases
unittest.main(argv=[''], verbosity=2, exit=False)
# Clean up
del TestDijkstra

testDijkstra1 (__main__.TestDijkstra) ... ok
testDijkstra2 (__main__.TestDijkstra) ... ok

----------------------------------------------------------------------
Ran 2 tests in 0.005s

OK
